# Ungraded Lab - Gradient Descent for Linear Regression

In the previous labs, we determined the optimal values of $w_0$ and $w_1$ manually. In this lab we will automate this process with gradient descent with one variable as described in lecture.

# Outline

- [Exercise 01- Compute Gradient](#ex01)
- [Exercise 02- Checking the Gradient](#ex02)
- [Exercise 03- Learning Parameters with Batch Gradient Descent](#ex-03)

In [ ]:
import matplotlib.pyplot as plt
import math 
import copy

## Problem Statement

Let's use the same two data points as before - a house with 1000 square feet sold for \\$200,000 and a house with 2000 square feet sold for \\$400,000.

That is our dataset contains has the following two points - 

| Size (feet$^2$)     | Price (1000s of dollars) |
| -------------------| ------------------------ |
| 1000               | 200                      |
| 2000               | 400                      |


In [ ]:
# Load our data set
X_train = [1000, 2000] #feature 
y_train = [200, 400]   #actual value

In [ ]:
## routine to plot the data points
def plt_house(X, y,f_w=None):
    plt.scatter(X, y, marker='x', c='r', label="Actual Value")

    # Set the title
    plt.title("Housing Prices")
    # Set the y-axis label
    plt.ylabel('Price (in 1000s of dollars)')
    # Set the x-axis label
    plt.xlabel('Size (feet^2)')
    # print predictions
    if f_w != None:
        plt.plot(X, f_w,  c='b', label="Our Prediction")
    plt.legend()
    plt.show()
    
plt_house(X_train,y_train)

### Compute_Cost
You produced this in the last lab, so this is supplied here for later use

In [ ]:
#Function to calculate the cost
def compute_cost(X, y, w):
   
    m = len(X)
    cost = 0
    
    for i in range(m):
    
        # Calculate the model prediction
        f_w = w[0] + w[1]*X[i]
        
        # Calculate the cost
        cost = cost + (f_w - y[i])**2

    total_cost = 1/(2*m) * cost

    return total_cost

## Gradient descent summary
So far in this course we have developed a linear model that predicts $f_{\mathbf{w}}(x)$ based a single input $x$ using trained parameters $w_0$,$w_1$.
$$f_\mathbf{w}(x)= w_0 + w_1x \tag{1}$$
In machine learning, we utilize input data to train the parameters $w_0$,$w_1$ by minimizing a measure of the error between our predictions $f_{\mathbf{w}}(x)$ and the actual data $y$. The measure is called the $cost$, $J(\mathbf{w})$. In training we measure the cost over all of our training samples $x^{(i)},y^{(i)}$
$$J(\mathbf{w}) = \frac{1}{2m} \sum\limits_{i = 0}^{m-1} (f_{\mathbf{w}}(x^{(i)}) - y^{(i)})^2\tag{2}$$ 
From calculus we know the partial derivitive of the cost relative to one of the parameters tells us how a small change in that parameter $w_j$, or $\Delta{w_j}$, causes a small change in $J(\mathbf{w})$, or $\Delta(J(w)$.

$$ \frac{\partial J(w)}{\partial w_j} \approx \frac{\Delta{J(w)}}{\Delta{w_j}}$$
Using that information, we can iteratively make small adjustments to $w_j$ that reduce the value of $J(\mathbf{w})$. This iterative process is called gradient descent. 



In lecture, *gradient descent* was described as:

$$\begin{align*}& \text{repeat until convergence:} \; \lbrace \newline \; & w_j := w_j -  \alpha \frac{\partial J(\mathbf{w})}{\partial w_j} \tag{3}  \; & \text{for j := 0,1}\newline & \rbrace\end{align*}$$
where, parameters $w_0$, $w_1$ are updated simultaneously.  
As in lecture:
$$
\begin{align}
 \frac{\partial J(\mathbf{w})}{\partial w_0}  &:= \frac{1}{m} \sum\limits_{i = 0}^{m-1} (f_{w}(x^{(i)}) - y^{(i)} \tag{4}\\
 \frac{\partial J(\mathbf{w})}{\partial w_1}  &:= \frac{1}{m} \sum\limits_{i = 0}^{m-1} (f_{w}(x^{(i)}) - y^{(i)})x^{(i)} \tag{5}\\
\end{align}
$$

<a name='ex01'></a>
## Exercise 01- Compute Gradient
We will implement a batch gradient descent algorithm for one variable. We'll need three functions. 
- compute_gradient implementing equation (4) and (5) above
- compute_cost implementing equation (2) above (code from previous lab)
- gradient_descent, utilizing compute_gradient and compute_cost, runs the iterative algorithm to find the parameters with the lowest cost.

## compute_gradient
<a name='ex-01'></a>
Implement `compute_gradient` which will return $\frac{\partial J(\mathbf{w})}{\partial w}$. A naming convention we will use in code when referring to gradients is to infer the dJ(w) and name variables for the parameter. For example, $\frac{\partial J(\mathbf{w})}{\partial w_0}$ will be `dw0`.

Please complete the `compute_gradient` function to:

- Create a list to store the gradient `dw`. 
- Loop over all examples in the training set `m`. 
    - Inside the loop, calculate the gradient update from each training example:
        - Calculate the model prediction `f`
        $$
        f_\mathbf{w}(x^{(i)}) =  w_0+ w_1x^{(i)} 
        $$
        - Calculate the gradient for $w_0$ and $w_1$
        $$
\begin{align}
\frac{\partial{J(w)}}{\partial{w_0}} &=  f_\mathbf{w}(x^{(i)}) - y^{(i)}  \\  
\frac{\partial{J(w)}}{\partial{w_1}} &= (f_\mathbf{w}(x^{(i)}) - y^{(i)})x^{(i)}  \\
\end{align}   
$$
        - Add these gradients to the total gradients `dw`
    
    - Compute total gradient by dividing by the number of examples `m`.
**Note** that this assignment continues to use python lists rather than the NumPy data structures that will be described in upcoming lectures. This will require writing some expressions 'per element' where later, these could be a single operation. Also note that these routines are specifically for one variable. Later labs and the weekly assignment will use more general cases.

<details>
<summary>
    <font size='3', color='darkgreen'><b>Hints</b></font>
</summary>

```
def compute_gradient(X, y, w): 
    """
    Computes the gradient for linear regression 
 
    Args:
      X : (array_like Shape (m,)) variable such as house size 
      y : (array_like Shape (m,)) actual value 
      w : (array_like Shape (2,)) Initial values of parameters of the model      
    Returns
      dw: (array_like Shape (2,)) The gradient of the cost w.r.t. the parameters w. 
                                   Note that dw has the same dimensions as w.
    """
    m = len(X)
    
    dw = [0,0]
    for i in range(m):        
        f   = w[0] + w[1]*X[i]
        dw0 = f-y[i]
        dw1 = (f-y[i])*X[i] 
        dw[0] = dw[0] + dw0
        dw[1] = dw[1] + dw1
    dw[0] = (1/m) * dw[0]
    dw[1] = (1/m) * dw[1]       
```

In [ ]:
def compute_gradient(X, y, w): 
    """
    Computes the gradient for linear regression 
 
    Args:
      X : (array_like Shape (m,)) variable such as house size 
      y : (array_like Shape (m,)) actual value 
      w : (array_like Shape (2,)) Initial values of parameters of the model      
    Returns
      dw: (array_like Shape (2,)) The gradient of the cost w.r.t. the parameters w. 
                                   Note that dw has the same dimensions as w.
    """
    m = len(X)
    dw = [0,0]   
    ### START CODE HERE ### 

    ### END CODE HERE ### 
       
    return dw

In [ ]:
#Compute and display gradient with w initialized to zeroes
initial_w = [0,0]
grad = compute_gradient(X_train, y_train, initial_w)
print('Gradient at initial w (zeros):', grad)

**Expected Output**:
```Gradient at initial w (zeros): [-300.0, -500000.0]```

In [ ]:
#Now, lets try setting w to a value we know, from previous labs, is the optimal value
initial_w = [0,0.2]
grad = compute_gradient(X_train, y_train, initial_w)
print('Gradient when w is set to optimal values:', grad)

**Expected Output**:
```Gradient when w is set to optimal values: [0.0, 0.0]```  
As we expected, the gradient is zero at the "bottom of the bowl".

In [ ]:
# one more test case to ensure we are using all the w values.
initial_w = [0.1,0.1]
grad = compute_gradient(X_train, y_train, initial_w)
print('Gradient:', grad)

**Expected Output**:
```Gradient: [-149.9, -249850.0]```  

### Checking the gradient
What do these gradient values mean?    
If you have taken calculus, you may recall an early lecture describing a derivative as:
$$\frac{df(x)}{dx} = \lim_{\Delta{x} \to 0} \frac{f(x+\Delta{x}) - f(x)}{\Delta{x}}$$
The derivative then is just a measure of how a small change in x, the $\Delta{x}$ above, changes $f(x)$.

Above, we calculated `dw1` or $\frac{\partial J(\mathbf{w})}{\partial w_1}$ to be -249850.0. That says that when $\mathbf{w} = [0.1,0.1]$, a small change in $w_1$ will result in a change in the **cost**, $J(\mathbf{w})$, that is -249850.0 times that change.  Note the change in notation  from $d$ to $\partial{}$ just indicates the J has multiple dependencies and that this is a derivative with respect to one of them - a partial derivative.

We can use this knowledge to perform a simple check of our implementation of the gradient.

<a name='ex02'></a>
## Exercise 2 
Let's check our gradient descent algorithm by 
calculating an approximation to the partial derivative with respect to $w_1$. We can't make $\Delta{x}$ go to zero as in the equation above, but we can just use a small value: 
$$ \frac{\partial J(\mathbf{w})}{\partial w_1} \approx\frac{Cost(w_0,w_1+\Delta)-Cost(w_0,w_1)}{\Delta{w_1}}$$
Of course, the same method can be applied to any of the parameters.

<details>
<summary>
    <font size='3', color='darkgreen'><b>Hints</b></font>
</summary>

```
# calculate a derivative and compare with our implementaion.
delta = 0.00001
w_check = [0.1,0.1]

# compute the gradient using our derivation and implementation
grad = compute_gradient(X_train, y_train, initial_w)

# compute point 1
c1 = compute_cost(X_train,y_train,w_check)

#increment parameter w_check[1] by delta, leave w_check[0] the same
w_check[0] = w_check[0]  # leave the same
w_check[1] = w_check[1] + delta

#compute point 2
c2 = compute_cost(X_train,y_train,w_check)
calculated_dw1 = (c2 - c1)/delta
print(f"calculated_dw1 {calculated_dw1:0.1f}, expected dw1 {grad[1]}" )#increment parameter w_check[1] by delta, leave w_check[0] the same      
```

In [ ]:
# calculate a derivative and compare with our implementaion.
delta = 0.00001
w_check = [0.1,0.1]

# compute the gradient using our derivation and implementation
### START CODE HERE ### 


# compute point 1


#increment parameter w_check[1] by delta, leave w_check[0] the same


#compute point 2

### END CODE HERE ### 

print(f"calculated_dw1 {calculated_dw1:0.1f}, expected dw1 {grad[1]}" )

**Expected Output**:  
```calculated_dw1 -249837.5, expected dw1 -249850.0```   
Not *exactly* the same, but close. The real derivative would take delta to zero. Try changing the value of delta.

<a name='ex-03'></a>
## Exercise 3 Learning parameters using batch gradient descent 

You will now find the optimal parameters of a linear regression model by using batch gradient descent. Recall batch refers to running all the examples in one batch. 
- You don't need to implement anything for this part. Simply run the cells below. 
- A good way to verify that gradient descent is working correctly is to look
at the value of $J(\mathbf{w})$ and check that it is decreasing with each step. 
- Assuming you have implemented the gradient and computed the cost correctly, your value of $J(\mathbf{w})$ should never increase and should converge to a steady value by the end of the algorithm.

In [ ]:
def gradient_descent(X, y, w_in, cost_function, gradient_function, alpha, num_iters): 
    """
    Performs batch gradient descent to learn theta. Updates theta by taking 
    num_iters gradient steps with learning rate alpha
    
    Args:
      X : (array_like Shape (m,)
      y : (array_like Shape (m,) )
      w_in : (array_like Shape (2,)) Initial values of parameters of the model
      alpha : (float) Learning rate
      num_iters : (int) number of iterations to run gradient descent
    Returns
      w : (array_like Shape (2,)) Updated values of parameters of the model after
          running gradient descent
    """
    
    # number of training examples
    m = len(X)
    w = copy.deepcopy(w_in) # avoid modifying global w
    # An array to store cost J and w's at each iteration primarily for graphing later
    J_history = []
    w_history = []
    
    for i in range(num_iters):
      
       # Calculate the gradient and update the parameters
        gradient = gradient_function(X, y, w)

        # Update Parameters 
        w[0] = w[0] - alpha * gradient[0]
        w[1] = w[1] - alpha * gradient[1]

        # Save cost J at each iteration
        if i<100000:      # prevent resource exhaustion 
            J_history.append( compute_cost(X, y, w))
        
        # Print cost every at intervals 10 times or as many iterations if < 10
        if i% math.ceil(num_iters/10) == 0:
            w_history.append([w[0],w[1]])
            print(f"Iteration {i:4}: Cost {J_history[-1]:8.2f}   ",
                  f"gradient: {gradient[0]:9.4f},{gradient[1]:14.4f}")
        
    return w, J_history, w_history #return w and J,w history for graphing

In [ ]:
# initialize parameters
w_init = [0,0]
# some gradient descent settings
iterations = 1000
alpha = 1.0e-8
# run gradient descent
w_final, J_hist, w_hist = gradient_descent(X_train ,y_train, w_init, compute_cost, compute_gradient, alpha, iterations)
print(f"w found by gradient descent: ({w_final[0]:8.4f},{w_final[1]:8.4f})")

**Expected Output**:  
```w found by gradient descent: (0.0001,0.2000)```  
As we expected, the calculated parameter values are very close to (0,0.2) from previous labs.

In [ ]:
print(f"1000 sqft house estimate {w_final[0] + w_final[1]*1000:0.2f} Thousand dollars")
print(f"1000 sqft house estimate {w_final[0] + w_final[1]*1200:0.2f} Thousand dollars")
print(f"2000 sqft house estimate {w_final[0] + w_final[1]*2000:0.2f} Thousand dollars")

In [ ]:
# plot cost vs iteration  
plt.plot(J_hist)
plt.title("Cost vs iteration")
plt.ylabel('Cost')
plt.xlabel('iteration step')
plt.show()

The plot shows that we rapidly reduced cost early. Recall from lecture that the gradient tends to be larger when further from the optimum creating larger step sizes. As you approach the final value, the gradient is smaller resulting in smaller step sizes.

## Plotting
Let's produce some of the fancy graphs that are popular for showing gradient descent. First we'll create some extra test cases.

In [ ]:
# generate some more paths
w_init = [400,0.6]
# some gradient descent settings
iterations = 1000
alpha = 1.0e-7
# run gradient descent
w2_final, J2_hist, w2_hist = gradient_descent(X_train ,y_train, w_init, compute_cost, compute_gradient, alpha, iterations)
print(f"w found by gradient descent: ({w2_final[0]:0.4f},{w2_final[1]:0.4f})")

Note, cost seems to have **plateaued**.

In [ ]:
#generate some more paths
w_init = [100,0.1]
# some gradient descent settings
iterations = 5
alpha = 1.0e-6  # larger alpha
# run gradient descent
w3_final, J3_hist, w3_hist = gradient_descent(X_train ,y_train, w_init, compute_cost, compute_gradient, alpha, iterations)
print(f"w found by gradient descent: ({w3_final[0]:0.4f},{w3_final[1]:0.4f})")

Note, cost is **increasing**!

In [ ]:
from mpl_toolkits.mplot3d import axes3d
import matplotlib.pyplot as plt
from matplotlib import cm
import numpy as np

w0 = np.arange(-500, 500, 5)
w1 = np.arange(-0.2, 0.8, 0.005)
w0,w1 = np.meshgrid(w0,w1)
z=np.zeros_like(w0)
n,_ = w0.shape
for i in range(n):
    for j in range(n):
        z[i][j] = compute_cost(X_train, y_train, [w0[i][j],w1[i][j]] )

   
fig = plt.figure(figsize=(24,6))

ax = fig.add_subplot(1, 2, 2)
CS = ax.contour(w1, w0, z,[0,50,1000,5000,10000,25000,50000])
plt.clabel(CS, inline=1, fmt='%1.0f', fontsize=10)
plt.title('Contour plot of cost J(w), vs w0,w1 with path of gradient descent')

w_sub = [ (i[1],i[0]) for i in w_hist]
for i in range(len(w_sub)-1):
    plt.annotate('', xy=w_sub[i + 1], xytext=w_sub[i],
                 arrowprops={'arrowstyle': '->', 'color': 'r', 'lw': 1},
                 va='center', ha='center')

w_sub = [ (i[1],i[0]) for i in w2_hist]
for i in range(len(w_sub)-1):
    plt.annotate('', xy=w_sub[i + 1], xytext=w_sub[i],
                 arrowprops={'arrowstyle': '->', 'color': 'b', 'lw': 1},
                 va='center', ha='center')
w_sub = [ (i[1],i[0]) for i in w3_hist]
for i in range(len(w_sub)-1):
    plt.annotate('', xy=w_sub[i + 1], xytext=w_sub[i],
                 arrowprops={'arrowstyle': '->', 'color': 'g', 'lw': 1},
                 va='center', ha='center')
  
ax.set_xlabel('w_1')
ax.set_ylabel('w_0')

plt.show()

<details>
<summary>
    <font size='3'><b>Expected graph</b></font>
</summary>
    <img src="./figures/ContourPlotLab3.PNG" alt="Contour Plot">
<\details>

What is this graph showing? The ellipses are describing the surface of the cost $J(\mathbf{w})$. The lines are the paths take from initial values of $(w_0,w_1)$ to their final values.  
The **red line** is our first run with w_init = (0,0). Gradient Descent successfully moves the parameters to (0,0.2) where cost is a minimum. But what about the Blue and Green lines?   
The **Blue** lines has w_init = (400,0.6) and alpha = 1.0e-7. Notice that while `w1` moves, `w0` doesn't seem to move. Why?  
The **Green** line has w_init = (100,0.1) and alpha = 1.0e-6. It never fully converges. Why?

<details>
<summary>
    <font size='3', color='darkgreen'><b>Hints</b></font>
</summary>
    
In next week's lectures we will cover some fine tuning of gradient descent that is required to get it to run well. The **blue line** is one of these cases. It it does not seem that `w0` is being updated, but it is, just slowly. `w1` is multiplied by $x_1$ which is the square footage of houses in the dataset, a value in the thousands. This makes `w1` update much more quickly than `w0`. Review the update equations (4) and (5) above. With alpha = 1.0e-7, it will take many iterations to update `w0` to the right value. 
    
Why not just increase the value of alpha? The **green** line demonstrates the problem with doing this. We use a larger value for alpha in that run and the solution _diverges_. The update for `w1` is so large that the cost is larger on each iteration rather than smaller.  If you run it long enough, you will generate a numerical overflow (try it). The lecture described this scenario. 
    
So, we have a situation where alpha is too big for `w1` but too small for `w0`. A means of dealing with this will be described next week. It involves _scaling_ or _normalizing_ the features in the data set so they fall within the same range. Once the data is normalized, alpha will impact all features evenly.
    
Another way to handle this is to select the largest value of alpha you can that doesn't cause the solution to diverge, and then run it a long time. Try this in the next section _if you have the time!_

In [ ]:
#TAKES A LONG TIME, 10 minutes or so.
w_init = [400,0.1]
# some gradient descent settings
iterations = 40000000
alpha = 7.0e-7
# run gradient descent
w4_final, J4_hist, w4_hist = gradient_descent(X_train ,y_train, w_init, compute_cost, compute_gradient, alpha, iterations)
print(f"w found by gradient descent: ({w4_final[0]:0.4f},{w4_final[1]:0.4f})")

In [ ]:
w0 = np.arange(-500, 500, 5)
w1 = np.arange(-0.2, 0.8, 0.005)
w0,w1 = np.meshgrid(w0,w1)
z=np.zeros_like(w0)
n,_ = w0.shape
for i in range(n):
    for j in range(n):
        z[i][j] = compute_cost(X_train, y_train, [w0[i][j],w1[i][j]] )

   
fig = plt.figure(figsize=(24,6))

ax = fig.add_subplot(1, 2, 2)
CS = ax.contour(w1, w0, z,[0,50,1000,5000,10000,25000,50000])
plt.clabel(CS, inline=1, fmt='%1.0f', fontsize=10)
plt.title('Contour plot of cost, w0 vs w1')

w_sub = [ (i[1],i[0]) for i in w_hist]
for i in range(len(w_sub)-1):
    plt.annotate('', xy=w_sub[i + 1], xytext=w_sub[i],
                 arrowprops={'arrowstyle': '->', 'color': 'r', 'lw': 1},
                 va='center', ha='center')

w_sub = [ (i[1],i[0]) for i in w4_hist]
for i in range(len(w_sub)-1):
    plt.annotate('', xy=w_sub[i + 1], xytext=w_sub[i],
                 arrowprops={'arrowstyle': '->', 'color': 'c', 'lw': 1},
                 va='center', ha='center')
  
ax.set_xlabel('w_1')
ax.set_ylabel('w_0')

plt.show()

The cyan line is our long-running solution. Scaling or Normalizing features will get us to the right solution faster. We will cover this next week.